<a href="https://colab.research.google.com/github/hidt4/python-compchem-book/blob/main/compchem_book_ch07.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## 7章　振動数計算をしてみよう

### 環境構築

#### Google Colab上にPsi4をインストール
2023年8月時点では問題なく動作していましたが

今後のColabの開発動向次第では動作しなくなる可能性があります

In [ ]:
!wget -c https://repo.continuum.io/miniconda/Miniconda3-latest-Linux-x86_64.sh
!chmod +x Miniconda3-latest-Linux-x86_64.sh
!bash ./Miniconda3-latest-Linux-x86_64.sh -b -f -p /usr/local
!conda install -q -y -c psi4 psi4 python=3.10
import sys
sys.path.append('/usr/local/lib/python3.10/site-packages')

--2023-07-18 01:59:28--  https://repo.continuum.io/miniconda/Miniconda3-latest-Linux-x86_64.sh
Resolving repo.continuum.io (repo.continuum.io)... 104.18.200.79, 104.18.201.79, 2606:4700::6812:c84f, ...
Connecting to repo.continuum.io (repo.continuum.io)|104.18.200.79|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://repo.anaconda.com/miniconda/Miniconda3-latest-Linux-x86_64.sh [following]
--2023-07-18 01:59:28--  https://repo.anaconda.com/miniconda/Miniconda3-latest-Linux-x86_64.sh
Resolving repo.anaconda.com (repo.anaconda.com)... 104.16.130.3, 104.16.131.3, 2606:4700::6810:8203, ...
Connecting to repo.anaconda.com (repo.anaconda.com)|104.16.130.3|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 103219356 (98M) [application/x-sh]
Saving to: ‘Miniconda3-latest-Linux-x86_64.sh’

Miniconda3-latest-L 100%[===================>]  98.44M   326MB/s    in 0.3s    

2023-07-18 01:59:28 (326 MB/s) - ‘Miniconda3-latest-Linu

In [ ]:
import os
import datetime
import numpy as np
import pandas as pd
import psi4

print(f'current time: {datetime.datetime.now()}')
print(f'python version:\n{sys.version}')
print(f'numpy version: {np.__version__}')
print(f'pandas version: {pd.__version__}')
print(f'psi4 version: {psi4.__version__}')

current time: 2023-07-18 02:02:11.390558
python version:
3.10.12 (main, Jun  7 2023, 12:45:35) [GCC 9.4.0]
numpy version: 1.22.4
pandas version: 1.5.3
psi4 version: 1.7


#### 必要なライブラリと関数の定義

In [ ]:
# 振動数可視化のためのライブラリ
!pip install py3Dmol
import py3Dmol

!git clone https://github.com/duerrsimon/normal-mode-jupyter.git
sys.path.append('/content/normal-mode-jupyter')
from helpers import show_normal_modes

Cloning into 'normal-mode-jupyter'...
remote: Enumerating objects: 23, done.
remote: Counting objects: 100% (23/23), done.
remote: Compressing objects: 100% (19/19), done.
remote: Total 23 (delta 8), reused 17 (delta 4), pack-reused 0
Unpacking objects: 100% (23/23), 801.95 KiB | 11.62 MiB/s, done.


In [ ]:
def show_3D(mol: psi4.core.Molecule) -> py3Dmol.view:
    """
    Psi4のMoleculeオブジェクトをpy3Dmolで描画する
    Args:
        mol: 描画対象の分子

    Returns:
        py3Dmol.view: py3Dmolの描画オブジェクト

    """
    view = py3Dmol.view(width=400, height=400)
    xyz = mol.save_string_xyz_file()
    view.addModel(xyz, 'xyz')
    view.setStyle({'stick': {}})
    view.setBackgroundColor('#e1e1e1')
    view.zoomTo()

    return view.show()

#### 計算資源の設定

In [ ]:
# 計算資源の確認（CPU, RAM）
!cat /proc/cpuinfo

processor	: 0
vendor_id	: GenuineIntel
cpu family	: 6
model		: 79
model name	: Intel(R) Xeon(R) CPU @ 2.20GHz
stepping	: 0
microcode	: 0xffffffff
cpu MHz		: 2199.998
cache size	: 56320 KB
physical id	: 0
siblings	: 8
core id		: 0
cpu cores	: 4
apicid		: 0
initial apicid	: 0
fpu		: yes
fpu_exception	: yes
cpuid level	: 13
wp		: yes
flags		: fpu vme de pse tsc msr pae mce cx8 apic sep mtrr pge mca cmov pat pse36 clflush mmx fxsr sse sse2 ss ht syscall nx pdpe1gb rdtscp lm constant_tsc rep_good nopl xtopology nonstop_tsc cpuid tsc_known_freq pni pclmulqdq ssse3 fma cx16 pcid sse4_1 sse4_2 x2apic movbe popcnt aes xsave avx f16c rdrand hypervisor lahf_lm abm 3dnowprefetch invpcid_single ssbd ibrs ibpb stibp fsgsbase tsc_adjust bmi1 hle avx2 smep bmi2 erms invpcid rtm rdseed adx smap xsaveopt arat md_clear arch_capabilities
bugs		: cpu_meltdown spectre_v1 spectre_v2 spec_store_bypass l1tf mds swapgs taa mmio_stale_data retbleed
bogomips	: 4399.99
clflush size	: 64
cache_alignment	: 64
addres

In [ ]:
!cat /proc/meminfo

MemTotal:       53474556 kB
MemFree:        40282332 kB
MemAvailable:   52002872 kB
Buffers:          217988 kB
Cached:         11660656 kB
SwapCached:            0 kB
Active:          1259020 kB
Inactive:       11155448 kB
Active(anon):        992 kB
Inactive(anon):   536440 kB
Active(file):    1258028 kB
Inactive(file): 10619008 kB
Unevictable:           0 kB
Mlocked:               0 kB
SwapTotal:             0 kB
SwapFree:              0 kB
Dirty:            175452 kB
Writeback:             0 kB
AnonPages:        533608 kB
Mapped:           450652 kB
Shmem:              1272 kB
KReclaimable:     472264 kB
Slab:             556496 kB
SReclaimable:     472264 kB
SUnreclaim:        84232 kB
KernelStack:        6240 kB
PageTables:        11144 kB
NFS_Unstable:          0 kB
Bounce:                0 kB
WritebackTmp:          0 kB
CommitLimit:    26737276 kB
Committed_AS:    2961796 kB
VmallocTotal:   34359738367 kB
VmallocUsed:       10224 kB
VmallocChunk:          0 kB
Percpu:          

In [ ]:
n_cpu = os.cpu_count()
ram = os.sysconf('SC_PAGE_SIZE') * os.sysconf('SC_PHYS_PAGES') / (1024 ** 3)

In [ ]:
# 環境に応じて計算資源を設定
psi4.set_num_threads(n_cpu)
psi4.set_memory(f'{ram * 0.9: .0f}GB')

46000000000

### 7.1 振動数計算とは何だろう

#### 水分子の計算

In [ ]:
# ログファイルの設定
psi4.set_output_file('h2o_optfreq_hf-sto3g.log')

PosixPath('h2o_optfreq_hf-sto3g.log')

In [ ]:
# 水分子の構造の設定
h2o = psi4.geometry('''
0 1
O       -0.7520847362      0.3573098626      0.0156794168
H        0.2372416200      0.3907947487     -0.0110698848
H       -1.0414501312      1.0972341870     -0.5754069255
''')

# 構造最適化計算の実行
psi4.optimize('hf/sto-3g', molecule=h2o)

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


-74.96599011059205

In [ ]:
# 最適化構造の出力
print(h2o.save_string_xyz())

0 1
 O    0.000000000000    0.000000000000   -0.071153222088
 H    0.758023512211    0.000000000000    0.564626634493
 H   -0.758023512211   -0.000000000000    0.564626634493



In [ ]:
show_3D(h2o)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
_, wfn = psi4.frequency('hf/sto-3g', molecule=h2o, return_wfn=True)

INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'function_kwargs': {}}
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=hf, basis=sto-3g, molecule=default, nre=8.907018662178986
INFO:psi4.driver.driver:Return gradient(): -74.96599011059207
INFO:psi4.driver.driver:[[ 0.00000000  0.00000000  0.00009575]
 [-0.00007207 -0.00000000 -0.00004787]
 [ 0.00007207  0.00000000 -0.00004787]]
INFO:psi4.driver.driver:Compute hessian(): method=hf, basis=sto-3g, molecule=default, nre=8.907018662178986
INFO:psi4.driver.driver:Return hessian(): -74.96599011059207
INFO:psi4.driver.driver:[[ 0.80411151 -0.00000000 -0.00000000 -0.40205576  0.00000000 -0.33725113 -0.40205576  0.00000000  0.33725113]
 [-0.00000000 -0.00007970  0.00000000  0.00000000  0.00003985 -0.00000000  0.00000000  0.00003985  0.00

##### normal_mode_writeを設定

In [ ]:
psi4.set_options({'normal_modes_write': True})
psi4.freq('hf/sto-3g', molecule=h2o)

INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=hf, basis=sto-3g, molecule=default, nre=8.907018662178986
INFO:psi4.driver.driver:Return gradient(): -74.96599011059203
INFO:psi4.driver.driver:[[ 0.00000000  0.00000000  0.00009575]
 [-0.00007207 -0.00000000 -0.00004787]
 [ 0.00007207  0.00000000 -0.00004787]]
INFO:psi4.driver.driver:Compute hessian(): method=hf, basis=sto-3g, molecule=default, nre=8.907018662178986
INFO:psi4.driver.driver:Return hessian(): -74.96599011059206
INFO:psi4.driver.driver:[[ 0.80411151 -0.00000000 -0.00000000 -0.40205576  0.00000000 -0.33725113 -0.40205576  0.00000000  0.33725113]
 [-0.00000000 -0.00007969  0.00000000  0.00000000  0.

-74.96599011059206

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('h2o_optfreq_hf-sto3g.default.2437.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((2170.2024971481, 0), (4140.6140327849, 1)…

#### エタン・エチレン・アセチレンの比較

##### エタン

In [ ]:
psi4.set_output_file('ethane_optfreq_hf-3-21g.log')

# エタン構造の定義
ethane = psi4.geometry('''
0 1
 C                 -1.25726143    1.25726139    0.00000000
 H                 -0.90060700    0.24845139    0.00000000
 H                 -0.90058859    1.76165958   -0.87365150
 H                 -2.32726143    1.25727458    0.00000000
 C                 -0.74391921    1.98321767    1.25740497
 H                  0.32608077    1.98303509    1.25750243
 H                 -1.10041427    2.99208399    1.25730739
 H                 -1.10075147    1.47893186    2.13105625
 ''')

# 構造最適化
_, wfn_c2h6 = psi4.optimize('hf/3-21g', molecule=ethane, return_wfn=True)

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


In [ ]:
print(ethane.save_string_xyz())

0 1
 C   -0.257110340788   -0.363599345233   -0.629778267049
 H    0.092333018412   -1.389657784225   -0.651309570724
 H    0.092516909398    0.130660271425   -1.529132701608
 H   -1.340968954296   -0.375958642969   -0.651410557462
 C    0.257110337271    0.363599337422    0.629778256091
 H    1.340969044448    0.375963902629    0.651407548108
 H   -0.092337977450    1.389656124873    0.651312622849
 H   -0.092511998640   -0.130663778727    1.529132789310



In [ ]:
show_3D(ethane)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
# 振動数計算
psi4.set_options({'normal_modes_write': True})
_, wfn_c2h6 = psi4.frequency('hf/3-21g',
                             molecule=ethane,
                             return_wfn=True,
                             ref_gradient=wfn_c2h6.gradient())

INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute hessian(): method=hf, basis=3-21g, molecule=default, nre=42.25161734328228
INFO:psi4.driver.driver:Return hessian(): -78.793940389323
INFO:psi4.driver.driver:[[ 0.62395990 -0.02253231 -0.03902747 -0.09004645  0.08635460  0.00105566 -0.09007767 -0.04227483  0.07535162
  -0.33823042 -0.00032563 -0.00062225 -0.10447487 -0.01297057 -0.02246577 -0.01061869 -0.02096464 -0.03631130
   0.00474271  0.00567472  0.01139980  0.00474549  0.00703866  0.01061971]
 [-0.02253231  0.60802842 -0.05519170  0.08736850 -0.30783300 -0.00025908 -0.04227472 -0.11993657  0.10652351
  -0.00133969 -0.05964858  0.00090899 -0.01297047 -0.11364569 -0.03177064  0.00024569 -0.00065930 -0.00074031
  -0.01553334 -0.01602384 -0.03448389  0.00703633  0.00971857  0.01501312]
 [-0.03902747 -0.05519170  0.54429739  0.00164089 -0.00191500 -0.05859903  0.0765226

In [ ]:
print(wfn_c2h6.frequencies().to_array())

[  313.69577377   921.68349523   921.68353281  1003.81275199
  1351.55793135  1351.55793855  1571.30752862  1579.66707263
  1677.07218765  1677.07221264  1678.02448576  1678.02451424
  3195.91712105  3200.12347291  3240.69532322  3240.69538484
  3267.54001745  3267.54007994]


In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('ethane_optfreq_hf-3-21g.default.6351.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((313.6939768507, 0), (921.6816466212, 1), …

##### エチレン

In [ ]:
psi4.set_output_file('ethylene_optfreq_hf-3-21g.log')

# エチレンの構造定義
ethylene = psi4.geometry('''
0 1
 C                 -0.31950208    0.90041492    0.00000000
 C                  1.00641392    0.90041492    0.00000000
 H                 -0.91308708    1.82445292    0.00000000
 H                 -0.91311808   -0.02359908   -0.00002200
 H                  1.59999892   -0.02362308   -0.00001900
 H                  1.60002992    1.82442892    0.00002600
''')

# 構造最適化
_, wfn_c2h4 = psi4.optimize('hf/3-21g',
              molecule=ethylene,
              return_wfn=True)

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


In [ ]:
show_3D(ethylene)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
# 振動数計算
psi4.set_options({'normal_modes_write': True})
_, wfn_c2h4 = psi4.frequency('hf/3-21g',
                             molecule=ethylene,
                             return_wfn=True,
                             ref_gradient=wfn_c2h4.gradient())

# 振動数を出力
print(wfn_c2h4.frequencies().to_array())

INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute hessian(): method=hf, basis=3-21g, molecule=default, nre=33.74960362472005
INFO:psi4.driver.driver:Return hessian(): -77.60098598130936
INFO:psi4.driver.driver:[[ 1.00532884 -0.00000328  0.00000114 -0.67047698  0.00000588 -0.00000584 -0.15072379  0.13674654  0.00000509
  -0.15072964 -0.13674962  0.00000027 -0.01669885 -0.00404545 -0.00000042 -0.01669960  0.00404594 -0.00000025]
 [-0.00000328  0.71514191  0.00001003  0.00000588 -0.14194962 -0.00000130  0.12796210 -0.29181486 -0.00000790
  -0.12796518 -0.29180894 -0.00000067  0.03792082  0.00521538  0.00000048 -0.03792034  0.00521612 -0.00000065]
 [ 0.00000114  0.00001003  0.15238287 -0.00000417 -0.00000127 -0.07123575  0.00000403 -0.00000679 -0.05030670
  -0.00000051 -0.00000180 -0.05030672  0.00000045 -0.00000009  0.00973314 -0.00000093 -0.00000009  0.00973315]
 [-0.6704

[  943.48568966  1114.67762462  1156.51271627  1165.85054693
  1387.43280003  1522.31569861  1639.76289561  1842.57497272
  3305.44923850  3327.23967573  3371.16909569  3402.67623239]


In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('ethylene_optfreq_hf-3-21g.default.6351.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((943.4848922897, 0), (1114.6748972861, 1),…

##### アセチレン

In [ ]:
psi4.set_output_file('acetylene_optfreq_hf-3-21g.log')

# アセチレンの構造定義
acetylene = psi4.geometry('''
0 1
 C                 -0.51037345    0.81742737    0.00000000
 C                  0.68462655    0.81742737    0.00000000
 H                 -1.57137345    0.81742737    0.00000000
 H                  1.74562655    0.81742737    0.00000000
''')

# 構造最適化
_, wfn_c2h2 = psi4.optimize('hf/3-21g',
                            molecule=acetylene,
                            return_wfn=True)

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


In [ ]:
show_3D(acetylene)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
# 振動数計算
psi4.set_options({'normal_modes_write': True})
_, wfn_c2h2 = psi4.frequency('hf/3-21g',
                             molecule=acetylene,
                             ref_gradient=wfn_c2h2.gradient(),
                             return_wfn=True)


INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute hessian(): method=hf, basis=3-21g, molecule=default, nre=25.08222106059547
INFO:psi4.driver.driver:Return hessian(): -76.39595134743178
INFO:psi4.driver.driver:[[ 1.78431719  0.00000000  0.00000000 -1.32930200 -0.00000000 -0.00000000 -0.46496966 -0.00000000 -0.00000000
   0.00995448  0.00000000 -0.00000000]
 [ 0.00000000  0.08934707 -0.00000000  0.00000000 -0.06069537  0.00000000 -0.00000000 -0.04139155  0.00000000
  -0.00000000  0.01273985 -0.00000000]
 [ 0.00000000 -0.00000000  0.08934707  0.00000000  0.00000000 -0.06069537 -0.00000000 -0.00000000 -0.04139155
  -0.00000000  0.00000000  0.01273985]
 [-1.32930200  0.00000000  0.00000000  1.78431744  0.00000000  0.00000000  0.00995435 -0.00000000 -0.00000000
  -0.46496979 -0.00000000 -0.00000000]
 [-0.00000000 -0.06069537  0.00000000  0.00000000  0.08934708 -0.00000000  0

In [ ]:
# 振動数を出力
print(wfn_c2h2.frequencies().to_array())

[  902.39906381   902.39907126   917.99916048   917.99916279
  2233.80274544  3596.13868970  3719.33988151]


In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetylene_optfreq_hf-3-21g.default.1549.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((902.3990638138, 0), (902.3990712594, 1), …

### 分子のIRスペクトルを求めてみよう

In [ ]:
def optfreq(mol: psi4.core.Molecule,
            theory: str) -> list[float, psi4.core.Wavefunction]:
    """
    分子の構造最適化と振動数計算を行う

    Args:
        mol (psi4.core.Molecule): 計算対象の分子
        theory: 計算レベル

    Returns:
        float: エネルギー
        psi4.core.Wavefunction: 計算のWavefunction

    """
    _, wfn = psi4.optimize(theory,
                           molecule=mol,
                           return_wfn=True)
    energy, wfn = psi4.frequency(theory,
                                 molecule=mol,
                                 ref_gradient=wfn.gradient(),
                                 return_wfn=True)

    return [energy, wfn]


def get_freqs(wavefunction: psi4.core.Wavefunction) -> np.ndarray:
    """
    Wavefunctionオブジェクトから振動数を取り出す
    Args:
        wavefunction: 対象のWavefunctionオブジェクト

    Returns:
        振動数のarrray

    """
    return wavefunction.frequencies().to_array()


# 計算レベルとログファイル名のリスト
theories = ['hf/sto-3g', 'hf/3-21g', 'mp2/6-31g', 'wb97x-d/aug-cc-pvdz']
logfiles = ['hf_sto3g', 'hf_3-21g', 'mp2_6-31g', 'wb97xd_aug-cc-pvdz']

#### アセトアルデヒド

In [ ]:
## アセトアルデヒドの構造を定義
acetaldehyde = psi4.geometry('''
0 1
 C                  0.11203320    0.61825725    0.00000000
 O                  1.33489796    0.61545082   -0.10440743
 H                 -0.48011015   -0.32114570    0.00198167
 C                 -0.70916294    1.92103771    0.00000000
 H                 -0.40304404    2.53560774   -0.82066734
 H                 -1.74874842    1.68735489   -0.09774644
 H                 -0.54626743    2.44532874    0.91841383
''')

##### HF/STO-3G

In [ ]:
psi4.set_output_file('acetaldehyde_hf-sto3g.log')
psi4.set_options({'normal_modes_write': True})

In [ ]:
# 構造最適化・振動数計算の実行
_, wfn = optfreq(acetaldehyde, 'hf/sto-3g')

Streaming output truncated to the last 5000 lines.
	interfrag_trust                =             0.5
	interfrag_trust_max            =             1.0
	interfrag_trust_min            =           0.001
	interfragment_connect          =             1.8
	intrafrag_hess                 =        SCHLEGEL
	intrafrag_trust                =             0.5
	intrafrag_trust_max            =             1.0
	intrafrag_trust_min            =           0.001
	irc_direction                  =         FORWARD
	irc_points                     =              20
	irc_step_size                  =             0.2
	keep_intcos                    =           False
	linear_bend_threshold          =            3.05
	linesearch                     =           False
	linesearch_step                =             0.1
	max_disp_g_convergence         =          0.0012
	max_energy_g_convergence       =           1e-06
	max_force_g_convergence        =          0.0003
	opt_coordinates                =       REDUNDANT

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -150.94629961546337
INFO:psi4.driver.driver:[[ 1.11832963 -0.08456772 -0.47220853 -0.82737243  0.08384986  0.40051669 -0.12569975 -0.09027965  0.06539662
  -0.15783231  0.06598324  0.00370769  0.01638090 -0.01933414 -0.00239063 -0.01900386  0.03820470  0.00367739
  -0.00480217  0.00614371  0.00130076]
 [-0.08456772  0.69127060 -0.11983774  0.08122358 -0.12235454 -0.02602707 -0.09301023 -0.28676051  0.13244546
   0.07348150 -0.26233464  0.01435479  0.02172785 -0.02394688 -0.00369770 -0.00505530  0.01170178  0.00029417
   0.00620032 -0.00757581  0.00246809]
 [-0.47220853 -0.11983774  0.54329068  0.40148870 -0.02751857 -0.28516300  0.06638900  0.13089589 -0.15401864
   0.00097088  0.01859573 -0.11619224 -0.01741466  0.01965291  0.00244579 -0.00473519  0.01560730  0.00228171
   0.02550980 -0.03739552  0.00735570]
 [-0.82737243  0.08122358  0.40148870  0.88240970 -0.10009957 -0.45094369 -0.02465688 -0.00089687  0.02716491
  -0.03233460  0.02148599  

In [ ]:
# 振動数の出力
print(get_freqs(wfn))

[  162.82529745   545.47044962   896.29144704  1062.38901959
  1284.89053227  1293.96044562  1619.50689446  1703.94085352
  1806.46125302  1808.20693078  2121.29926669  3541.61981915
  3564.77457987  3739.48973264  3763.10242720]


In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetaldehyde_hf-sto3g.default.2437.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((162.5115402487, 0), (545.4663106657, 1), …

##### まとめて計算

In [ ]:
# 構造最適化と振動数計算の実行
co_aldehyde = []

for theory, logfile in zip(theories, logfiles):
    filename = f'acetaldehyde_{logfile}.log'
    psi4.set_output_file(filename)

    _, wfn = optfreq(acetaldehyde, theory)
    co_aldehyde.append(get_freqs(wfn)[10])

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -150.9462996246424
INFO:psi4.driver.driver:[[ 1.11801091 -0.08488597 -0.47249147 -0.82703801  0.08397445  0.40080393 -0.12565812 -0.09017966  0.06539587
  -0.15788058  0.06607483  0.00370602  0.01638593 -0.01934250 -0.00238851 -0.01900995  0.03820577  0.00367741
  -0.00481018  0.00615307  0.00129675]
 [-0.08488597  0.69128268 -0.11980076  0.08135905 -0.12236935 -0.02613344 -0.09292129 -0.28663844  0.13249815
   0.07356085 -0.26244031  0.01435944  0.02174065 -0.02396328 -0.00368879 -0.00504906  0.01169935  0.00029529
   0.00619577 -0.00757065  0.00247012]
 [-0.47249147 -0.11980076  0.54381934  0.40176155 -0.02761933 -0.28555541  0.06639747  0.13094055 -0.15415032
   0.00096958  0.01861072 -0.11619476 -0.01740907  0.01965455  0.00244175 -0.00474061  0.01562032  0.00228484
   0.02551254 -0.03740605  0.00735456]
 [-0.82703801  0.08135905  0.40176155  0.88202418 -0.10024761 -0.45125466 -0.02462098 -0.00088912  0.02717882
  -0.03232120  0.02149231  0

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


...

Optimizer: Optimization complete!


INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-10, 'E_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-10, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=mp2, basis=6-31g, molecule=C2H4O, nre=68.3463899383929
INFO:psi4.driver.driver:Return gradient(): -153.1555042264605
INFO:psi4.driver.driver:[[-0.00025213  0.00004920  0.00022713]
 [ 0.00017939 -0.00001670 -0.00012530]
 [ 0.00003155 -0.00001869 -0.00004878]
 [ 0.00004099 -0.00005024 -0.00004830]
 [-0.00000351  0.00002296 -0.00000619]
 [ 0.00000473  0.00001418  0.00001216]
 [-0.00000102 -0.00000070 -0.00001072]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 68.3391343764416
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-10, 'E_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-10, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'fun

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.task_base:<<< JSON launch ... c1 69.63651602453918
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=wb97x-d, basis=aug-cc-pvdz, molecule=C2H4O, nre=69.63651602453918
INFO:psi4.driver.driver:Return gradient(): -153.79952838789626
INFO:psi4.driver.driver:[[ 0.00018637  0.00004211 -0.00013425]
 [-0.00017435  0.00000381  0.00011226]
 [-0.00003283 -0.00012553  0.00007313]
 [-0.00006237 -0.00001387  0.00000671]
 [ 0.00002696 -0.00002956 -0.00001617]
 [-0.00002331  0.00005559  0.00005333]
 [-0.00006388  0.00000372  0.00000954]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 69.62816123805811
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE':

In [ ]:
print(co_aldehyde)
print(1727/np.array(co_aldehyde))

[2121.4265843676703, 1926.134389729196, 1648.3365840535303, 1846.4809259958945]
[ 0.8140748365867979  0.8966144881732820  1.0477229084808781
  0.9352926291770640]


#### アセトアミド

In [ ]:
# アセトアミドの構造定義
acetamide = psi4.geometry('''
0 1
 C                  0.11203320    0.61825725    0.00000000
 O                  1.33489796    0.61545082   -0.10440743
 C                 -0.70916294    1.92103771    0.00000000
 H                 -0.40304404    2.53560774   -0.82066734
 H                 -1.74874842    1.68735489   -0.09774644
 H                 -0.54626743    2.44532874    0.91841383
 N                 -0.67183364   -0.62530452    0.00262330
 H                 -0.42379451   -1.17736195   -0.79343523
 H                 -0.47841040   -1.13949341    0.83820527
 ''')

##### HF/STO-3G

In [ ]:
psi4.set_output_file('acetamide_hf-sto3g.log')
_, wfn = optfreq(acetamide, 'hf/sto-3g')
print(get_freqs(wfn))

Streaming output truncated to the last 5000 lines.
	   0.000555  -0.001126  -0.000990  -0.012720   0.013716   0.000067  -0.010920
	  -0.010003   0.009572   0.005096   0.003523  -0.003001  -0.004574  -0.002683
	  -0.001765   0.017810

INFO:psi4.optking.molsys:Projected (PHP) Hessian matrix
	   0.924876  -0.015452   0.047656  -0.030500  -0.028773  -0.033218  -0.033956
	  -0.034710   0.004841  -0.003917  -0.012634  -0.006478  -0.028727   0.012275
	   0.001746  -0.014272  -0.000602   0.006463   0.006061   0.011309  -0.005827
	  -0.006097  -0.008542   0.013373   0.008958   0.001106  -0.003309   0.006897
	   0.006627   0.004182
	  -0.015452   0.291732  -0.008087   0.018123   0.017229   0.021415   0.035987
	   0.041242  -0.001287   0.002553   0.006093  -0.015774   0.004607   0.005144
	   0.003594  -0.008488   0.000388  -0.004084  -0.003825  -0.007826   0.000433
	   0.001585   0.003014   0.002664  -0.014098   0.006347  -0.010416  -0.003267
	  -0.002114  -0.000686
	   0.047656  -0.008087   0.33

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -205.28272537234517
INFO:psi4.driver.driver:[[ 1.08459163  0.00852818 -0.49363100 -0.76885615 -0.01444200  0.40026255 -0.15807396  0.06089350  0.02407687
   0.01469542 -0.01839738 -0.00807576 -0.01821406  0.03583001  0.01525985 -0.00281520  0.00194871  0.00288905
  -0.14732162 -0.08830973  0.08799215  0.01482978  0.03595025 -0.01873041 -0.01883584 -0.02200154 -0.01004330]
 [ 0.00852818  0.71639263 -0.02399263 -0.01192663 -0.11632411  0.00798318  0.07028680 -0.24093463 -0.03193680
   0.02307150 -0.02495729 -0.01248769 -0.00315449  0.00657107  0.00196281 -0.00168527  0.00333327  0.00139944
  -0.04290252 -0.31880307  0.07682870 -0.03382980 -0.03323707 -0.00436548 -0.00838778  0.00795920 -0.01539153]
 [-0.49363100 -0.02399263  0.53037136  0.39923268  0.00830195 -0.30410000  0.02382685 -0.03021397 -0.12369548
  -0.01079814  0.01220115  0.00503575 -0.00502193  0.01587457  0.00710302  0.02591081 -0.03842927 -0.00501332
   0.04635533  0.01243243 -0.101

[  129.0127003543328215   353.3840270749474826   428.3763563249314643
   575.8343974140290129   582.6558942331944309   817.5348349101515169
   960.5937343096734367  1158.4216169802100467  1226.3605515053277486
  1350.9823846336062161  1507.7226383110639745  1703.3603236455624028
  1804.6969060517835715  1805.7293971443987175  1950.8802467640412033
  2134.3496512604474447  3570.1308204880951962  3746.4108831375133377
  3768.3980890539792199  3952.1344180394776231  4153.1656526850110822]


In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetamide_hf-sto3g.default.2437.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((130.5656345482, 0), (354.2618235939, 1), …

##### まとめて計算

In [ ]:
co_amide = []

for theory, logfile in zip(theories, logfiles):
    filename = f'acetamide_{logfile}.log'
    psi4.set_output_file(filename)

    _, wfn = optfreq(acetamide, theory)
    co_amide.append(get_freqs(wfn)[15])

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -205.28272535568607
INFO:psi4.driver.driver:[[ 1.08439783  0.00840639 -0.49399699 -0.76872704 -0.01445180  0.40045790 -0.15806876  0.06093889  0.02416262
   0.01471045 -0.01841704 -0.00809875 -0.01821642  0.03581968  0.01527978 -0.00283681  0.00197384  0.00289385
  -0.14725846 -0.08818989  0.08808343  0.01482279  0.03593789 -0.01876445 -0.01882357 -0.02201797 -0.01001740]
 [ 0.00840639  0.71646039 -0.02411656 -0.01192491 -0.11630845  0.00800131  0.07030334 -0.24101411 -0.03206502
   0.02307573 -0.02496174 -0.01249409 -0.00313232  0.00654205  0.00195579 -0.00170605  0.00336476  0.00141268
  -0.04282717 -0.31881308  0.07706056 -0.03381712 -0.03323665 -0.00434713 -0.00837790  0.00796683 -0.01540754]
 [-0.49399699 -0.02411656  0.53085690  0.39949834  0.00832614 -0.30438938  0.02385619 -0.03026429 -0.12375071
  -0.01076236  0.01217409  0.00502418 -0.00503341  0.01589812  0.00713068  0.02590411 -0.03843680 -0.00504455
   0.04639607  0.01258558 -0.101

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


...

Optimizer: Optimization complete!


INFO:psi4.driver.task_base:<<< JSON launch ... c1 119.67619176748637
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-10, 'E_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-10, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=mp2, basis=6-31g, molecule=C2H5NO, nre=119.67619176748637
INFO:psi4.driver.driver:Return gradient(): -208.3037497705774
INFO:psi4.driver.driver:[[-0.00024835 -0.00000405 -0.00042934]
 [ 0.00008620  0.00000641  0.00015732]
 [ 0.00006985  0.00000708  0.00014266]
 [-0.00000684 -0.00001302  0.00001793]
 [ 0.00003849 -0.00002026 -0.00000789]
 [-0.00001075  0.00002451 -0.00000936]
 [ 0.00005785 -0.00005774  0.00010372]
 [-0.00000352  0.00003643  0.00001007]
 [ 0.00001707  0.00002063  0.00001487]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 119.67330200815739
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVER

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.task_base:<<< JSON launch ... c1 121.56913130018145
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=wb97x-d, basis=aug-cc-pvdz, molecule=C2H5NO, nre=121.56913130018145
INFO:psi4.driver.driver:Return gradient(): -209.18201186985425
INFO:psi4.driver.driver:[[ 0.00005518 -0.00009660 -0.00001467]
 [-0.00011561 -0.00003420  0.00007913]
 [-0.00000923 -0.00006152  0.00000033]
 [-0.00003261 -0.00006313  0.00003154]
 [-0.00004952 -0.00005405  0.00004681]
 [-0.00004984 -0.00005675  0.00003707]
 [-0.00004380 -0.00002441  0.00003136]
 [-0.00000805 -0.00004601  0.00001118]
 [-0.00002312 -0.00006214  0.00002304]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 121.56561038504547
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08

In [ ]:
print(co_amide)
print(1681/np.array(co_amide))

[2134.5473809207315, 1918.6566902618576, 1727.102365813743, 1803.3784741792147]
[ 0.7875205840007660  0.8761338120216690  0.9733065238480978
  0.9321393285261910]


#### 塩化アセチル

In [ ]:
acetylchloride = psi4.geometry('''
0 1
 C                  0.11203320    0.61825725    0.00000000
 O                  1.33489796    0.61545082   -0.10440743
 C                 -0.70916294    1.92103771    0.00000000
 H                 -0.40304404    2.53560774   -0.82066734
 H                 -1.74874842    1.68735489   -0.09774644
 H                 -0.54626743    2.44532874    0.91841383
 Cl                -0.82647404   -0.87063304    0.00314082
''')

##### HF/STO-3G

In [ ]:
psi4.set_output_file('acetylchloride_hf-sto3g.log')
_, wfn = optfreq(acetylchloride, 'hf/sto-3g')
get_freqs(wfn)

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -604.9673969778522
INFO:psi4.driver.driver:[[ 1.13895236 -0.18863516 -0.38780967 -0.91674475  0.10429205  0.36442743 -0.15192104  0.08093597  0.00269262
   0.01196476 -0.01772717 -0.00175415 -0.01848718  0.03867805  0.00734339 -0.00753289  0.01035778 -0.00038494
  -0.05623124 -0.02790152  0.01548533]
 [-0.18863516  0.52934853  0.00947437  0.13764193 -0.11042476 -0.05216952  0.08350752 -0.24005380 -0.00748494
   0.02120753 -0.02461261 -0.00423347 -0.00281754  0.00801007  0.00120310  0.00417816 -0.00536331  0.00069315
  -0.05508245 -0.15690412  0.05251731]
 [-0.38780967  0.00947437  0.36743512  0.35685527 -0.03698748 -0.21829769  0.00210454 -0.00631244 -0.10515675
  -0.01060709  0.01350549  0.00103074 -0.00754175  0.01897212  0.00385190  0.02533814 -0.03879345  0.00626733
   0.02166057  0.04014137 -0.05513065]
 [-0.91674475  0.13764193  0.35685527  0.98130198 -0.10992647 -0.41000861 -0.02872514  0.01168676  0.02288885
   0.00221263 -0.00291061 -0

array([  152.8683037113556793,   349.3922571287190522,
         506.5113007797740465,   545.1275918436813299,
         728.4618722511207807,  1140.8706790839335099,
        1227.2544353304781453,  1306.9994433124120405,
        1682.5757279640790784,  1774.6606318511271638,
        1779.4959011806809031,  2149.7646020692623097,
        3573.2714585328162684,  3755.0088487879643253,
        3765.1404942240274067])

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetylchloride_hf-sto3g.default.2437.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((151.5764018714, 0), (349.360245467, 1), (…

##### まとめて計算

In [ ]:
co_chloride = []

for theory, logfile in zip(theories, logfiles):
    filename = f'acetylchloride_{logfile}.log'
    psi4.set_output_file(filename)

    _, wfn = optfreq(acetylchloride, theory)
    co_chloride.append(get_freqs(wfn)[11])

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -604.9673969672932
INFO:psi4.driver.driver:[[ 1.13898519 -0.18864906 -0.38802361 -0.91678373  0.10442976  0.36462017 -0.15191139  0.08088642  0.00268819
   0.01196815 -0.01773176 -0.00175243 -0.01847767  0.03866959  0.00734427 -0.00753244  0.01035336 -0.00039003
  -0.05624810 -0.02795830  0.01551344]
 [-0.18864906  0.52938620  0.00947517  0.13775258 -0.11043515 -0.05224185  0.08346597 -0.23998585 -0.00748178
   0.02121291 -0.02462342 -0.00423026 -0.00281614  0.00800854  0.00120322  0.00416908 -0.00535644  0.00069730
  -0.05513535 -0.15699389  0.05257817]
 [-0.38802361  0.00947517  0.36758242  0.35704483 -0.03706250 -0.21842147  0.00210473 -0.00631052 -0.10516752
  -0.01060265  0.01350514  0.00103052 -0.00753999  0.01897611  0.00385165  0.02532682 -0.03878367  0.00627592
   0.02168987  0.04020027 -0.05515152]
 [-0.91678373  0.13775258  0.35704483  0.98133002 -0.11003336 -0.41022224 -0.02869845  0.01168653  0.02288784
   0.00221122 -0.00290890 -0

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


...

Optimizer: Optimization complete!


INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-10, 'E_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-10, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=mp2, basis=6-31g, molecule=C2ClH3O, nre=143.20869695475872
INFO:psi4.driver.driver:Return gradient(): -612.0975195536728
INFO:psi4.driver.driver:[[-0.00033421  0.00030078  0.00029844]
 [ 0.00021938 -0.00015695 -0.00014967]
 [ 0.00011502 -0.00015766 -0.00008960]
 [-0.00005549  0.00000025  0.00001836]
 [ 0.00000251  0.00002773  0.00001397]
 [ 0.00000199  0.00000189 -0.00002308]
 [ 0.00005080 -0.00001604 -0.00006842]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 143.2061508125264
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-10, 'E_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-10, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1',

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.task_base:<<< JSON launch ... c1 148.55863682342118
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'PARENT_SYMMETRY': 'C1', 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute gradient(): method=wb97x-d, basis=aug-cc-pvdz, molecule=C2ClH3O, nre=148.55863682342118
INFO:psi4.driver.driver:Return gradient(): -613.4241030608624
INFO:psi4.driver.driver:[[ 0.00000525 -0.00010811  0.00003148]
 [-0.00003501 -0.00006385  0.00002943]
 [ 0.00001389  0.00000965 -0.00002426]
 [ 0.00004134 -0.00005704 -0.00001561]
 [ 0.00002482 -0.00000619 -0.00000807]
 [ 0.00002176 -0.00001384  0.00001075]
 [-0.00004898  0.00004982  0.00000894]]
INFO:psi4.driver.task_base:<<< JSON launch ... c1 148.55598034005624
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__D_CONVERGENCE': 1e-08, 'SCF__E_CONVERGENCE': 1e-08, 'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRI

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetylchloride_hf_3-21g.default.56545.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((185.0415796597, 0), (347.5493558817, 1), …

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetylchloride_mp2_6-31g.C2ClH3O.56545.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((142.6895446521, 0), (328.542648506, 1), (…

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('acetylchloride_wb97xd_aug-cc-pvdz.C2ClH3O.56545.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((215.3555100753, 0), (359.8715088876, 1), …

In [ ]:
print(co_chloride)
1806/np.array(co_chloride)

[2149.9478536322213, 2042.3442867309363, 1758.8438417381988, 1917.7534612304419]


array([ 0.8400203739587730,  0.8842779406653131,  1.0268108840266335,
        0.9417268885236477])

### 熱力学的パラメータを求めてみよう

#### シクロプロパン

In [ ]:
psi4.set_options({'normal_modes_write': True})

In [ ]:
psi4.set_output_file('cyclopropane.log')

PosixPath('cyclopropane.log')

In [ ]:
cyclopropane = psi4.geometry('''
0 1
 C                  0.16445241    0.38365967    0.00286974
 C                  1.66556741    0.38365967    0.00286974
 C                  0.91498241    1.68363467    0.00286974
 H                 -0.37214359    0.07378467   -0.91098826
 H                 -0.37214359    0.07378467    0.91672774
 H                  2.20212841    0.07389267   -0.91101826
 H                  2.20212841    0.07389267    0.91675774
 H                  0.91475941    2.30316267    0.91681374
 H                  0.91475941    2.30316267   -0.91107426
 ''')

In [ ]:
energy_cpropane, wfn_cpropane = optfreq(cyclopropane, 'hf/cc-pvdz')

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -117.06721208340187
INFO:psi4.driver.driver:[[ 0.37498216 -0.19746535  0.00000000 -0.01880698  0.02827692 -0.00000000 -0.20154252  0.07722756  0.00000000
  -0.06790884  0.04406648 -0.07078419 -0.06790884  0.04406648  0.07078419  0.00081365 -0.00930442  0.00172337
   0.00081365 -0.00930442 -0.00172337 -0.01022114  0.01121838  0.00398575 -0.01022114  0.01121838 -0.00398575]
 [-0.19746535  0.60291619 -0.00000000 -0.02824589 -0.26243627 -0.00000000  0.13374869 -0.07970014  0.00000000
   0.04406697 -0.11877223  0.12257861  0.04406697 -0.11877223 -0.12257861  0.00484943 -0.01132631  0.00360719
   0.00484943 -0.01132631 -0.00360719 -0.00293512 -0.00029136 -0.00031059 -0.00293512 -0.00029136  0.00031059]
 [ 0.00000000 -0.00000000  0.73458716 -0.00000000 -0.00000000 -0.08596230  0.00000000  0.00000000 -0.08596316
  -0.06787075  0.11753229 -0.28668839  0.06787075 -0.11753229 -0.28668839  0.01697542 -0.02693161  0.00267869
  -0.01697542  0.02693161  0.002

In [ ]:
print(f'cyclopropane freqs:\n{get_freqs(wfn_cpropane)}')
cyclopropane_H = psi4.variable('ENTHALPY')

cyclopropane freqs:
[  786.8803254655430237   786.8824584542088587   909.0525132163604667
   949.5333671028422486   949.5402309241593457  1163.1466506635765654
  1163.1562814385824822  1190.5550177020663796  1242.1318949624758261
  1292.0459187807268790  1301.0505513180064554  1301.0549038525737160
  1566.0419686817172078  1566.0431425213130296  1638.1625332143296419
  3275.0084168762132322  3275.0106039183810935  3291.1737469298886936
  3358.7026506846809752  3358.7041020367673809  3381.6257896001507106]


In [ ]:
show_3D(cyclopropane)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('cyclopropane.default.1549.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((786.8803254655, 0), (786.8824584542, 1), …

#### メタン

In [ ]:
psi4.set_output_file('methane.log')

methane = psi4.geometry('''
0 1
 C                 -0.40248963    0.33609958    0.00000000
 H                 -0.04583521   -0.67271042    0.00000000
 H                 -0.04581679    0.84049777    0.87365150
 H                 -0.04581679    0.84049777   -0.87365150
 H                 -1.47248963    0.33611276    0.00000000
 ''')

In [ ]:
energy_methane, wfn_methane = optfreq(methane, 'hf/cc-pvdz')

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -40.19871708204559
INFO:psi4.driver.driver:[[ 0.60649731  0.00000002  0.00000000 -0.08593360  0.09289465 -0.00000000 -0.08593703 -0.04644914 -0.08045298
  -0.08593703 -0.04644914  0.08045298 -0.34868964  0.00000362  0.00000000]
 [ 0.00000002  0.60649725 -0.00000000  0.09289465 -0.31584768  0.00000000 -0.04644914 -0.11877895 -0.11377472
  -0.04644914 -0.11877895  0.11377472  0.00000362 -0.05309166 -0.00000000]
 [ 0.00000000 -0.00000000  0.60649733 -0.00000000  0.00000000 -0.05309167 -0.08045298 -0.11377472 -0.25015700
   0.08045298  0.11377472 -0.25015700  0.00000000 -0.00000000 -0.05309167]
 [-0.08593360  0.09289465 -0.00000000  0.08660669 -0.10216981 -0.00000000  0.00414795 -0.01289362  0.00153078
   0.00414795 -0.01289362 -0.00153078 -0.00896899  0.03506239 -0.00000000]
 [ 0.09289465 -0.31584768  0.00000000 -0.10216981  0.33947679 -0.00000000  0.00512081 -0.01335695  0.00142907
   0.00512081 -0.01335695 -0.00142907 -0.00096646  0.00308480 -0.

In [ ]:
print(f'methane freqs:\n{get_freqs(wfn_methane)}')
methane_H = psi4.variable('ENTHALPY')

methane freqs:
[ 1433.9965807695753028  1433.9966392333151362  1433.9966495771773225
  1648.4129126151410674  1648.4129191348272343  3164.0884211970937940
  3284.8447893310044492  3284.8448845514794812  3284.8449001994690661]


In [ ]:
show_3D(methane)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
# 振動数を可視化（自分で作成したファイル名を指定する）
show_normal_modes('methane.CH4.1008.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((1457.0645145136, 0), (1457.0674498216, 1)…

#### エタン

In [ ]:
psi4.set_output_file('ethane.log')

ethane = psi4.geometry('''
0 1
 C                 -0.40248963    0.33609958    0.00000000
 H                 -0.04583521   -0.67271042    0.00000000
 H                 -0.04581679    0.84049777   -0.87365150
 H                 -1.47248963    0.33611276    0.00000000
 C                  0.11085259    1.06205585    1.25740497
 H                  1.18085259    1.06202576    1.25741439
 H                 -0.24578624    2.07087137    1.25739542
 H                 -0.24583592    0.55766838    2.13105626
 ''')

In [ ]:
energy_ethane, wfn_ethane = optfreq(ethane, 'hf/cc-pvdz')

INFO:psi4.optking.optwrapper:Creating a UserComputer
INFO:psi4.optking.optwrapper:
    			-----------------------------------------

    			 OPTKING 3.0: for geometry optimizations 

    			     By R.A. King, Bethel University     

    			        with contributions from          

    			    A.V. Copan, J. Cayton, A. Heide      

    			-----------------------------------------

    
INFO:psi4.optking.optwrapper:
		 -- Optimization Parameters --
	accept_symmetry_breaking       =           False
	alg_geom_maxiter               =              50
	bt_dx_conv                     =           1e-07
	bt_dx_rms_change_conv          =           1e-12
	bt_max_iter                    =              25
	cart_hess_read                 =           False
	consecutive_backsteps_allowed  =               0
	conv_max_DE                    =           1e-06
	conv_max_disp                  =          0.0012
	conv_max_force                 =          0.0003
	conv_rms_disp                  =              -1

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -79.23493503604728
INFO:psi4.driver.driver:[[ 0.62227625 -0.01389550 -0.02406792 -0.08660242  0.08658095  0.00111057 -0.08660824 -0.04233139  0.07554359
  -0.33969813 -0.00131427 -0.00228736 -0.10903722 -0.02304086 -0.03990831 -0.00981597 -0.01910673 -0.03309397
   0.00474261  0.00612810  0.01159684  0.00474311  0.00697968  0.01110656]
 [-0.01389550  0.61245143 -0.03403629  0.08815729 -0.30955567 -0.00203089 -0.04233137 -0.11653577  0.10682850
  -0.00289062 -0.05645990  0.00037016 -0.02304086 -0.12532828 -0.05643738  0.00098143  0.00015465  0.00060115
  -0.01395984 -0.01440422 -0.03100141  0.00697946  0.00967777  0.01570616]
 [-0.02406792 -0.03403629  0.57314899  0.00202061 -0.00460508 -0.05603257  0.07736384  0.10940262 -0.24904665
  -0.00501766  0.00037022 -0.05603264 -0.03990830 -0.05643738 -0.19049774  0.00169950  0.00060036  0.00084751
  -0.00000028  0.00180258  0.00084779 -0.01208979 -0.01709703 -0.02323469]
 [-0.08660242  0.08815729  0.0

In [ ]:
print(f'ethane freqs:\n{get_freqs(wfn_ethane)}')
ethane_H = psi4.variable('ENTHALPY')

ethane freqs:
[  338.5330611900564577   877.4500845396772775   877.4500854644135188
  1062.0825140048634694  1313.0131112995095464  1313.0131130213280812
  1501.9015083354343005  1540.3087826863111331  1596.3332356767496094
  1596.3332368507212777  1599.8088290372272695  1599.8088299433834436
  3169.4547410250629582  3179.8852976148168636  3230.3451931974882427
  3230.3452022520559694  3255.8503903426812940  3255.8503995560076874]


In [ ]:
show_3D(ethane)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
show_normal_modes('ethane.default.2404.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((313.6812551406, 0), (921.6784701269, 1), …

#### アイソデスミック反応による推定

In [ ]:
au2kcal = psi4.constants.hartree2kcalmol

In [ ]:
isodesmic_h = au2kcal * (3 * ethane_H - (cyclopropane_H + 3 * methane_H))
print(f'estimated strain energy using isodesmic reaction: {-isodesmic_h: .2f} kcal/mol')

estimated strain energy using isodesmic reaction:  21.88 kcal/mol


#### メチルシクロヘキサン

エクアトリアル置換

In [ ]:
psi4.set_output_file('equatorial.log')

PosixPath('equatorial.log')

In [ ]:
equatorial = psi4.geometry('''
0 1
 C                 -2.15838901   -1.67295376    0.00000000
 C                 -0.64328301   -1.67295376    0.00000000
 C                 -0.09135201   -0.26187576    0.00000000
 C                 -0.64101501    0.54266124    1.16066100
 C                 -2.15614001    0.54332224    1.16017200
 C                 -2.70894001   -0.86729876    1.15887600
 H                  1.02724699   -0.29586676    0.06271400
 H                 -0.27073401   -2.21858776    0.90656200
 H                 -0.26798901   -2.22281276   -0.90191000
 H                 -2.53107701   -1.23992476   -0.96538500
 H                 -2.53398601   -2.72717376    0.06350200
 H                 -0.26848001    0.10781624    2.12527200
 H                 -0.26499201    1.59679824    1.09866600
 H                 -2.53146001    1.09275024    2.06228600
 H                 -2.52799501    1.08992324    0.25384900
 H                 -2.44293601   -1.37302076    2.12419100
 H                 -0.35997001    0.24375724   -0.96454600
 C                 -4.24559913   -0.81913202    1.06966430
 H                 -4.63527674   -1.81550142    1.08696717
 H                 -4.63411695   -0.26971208    1.90158475
 H                 -4.53508198   -0.33871606    0.15845621
 ''')

In [ ]:
_, equatorial_wfn = optfreq(equatorial, 'hf/cc-pvdz')

Streaming output truncated to the last 5000 lines.
INFO:psi4.optking.convcheck:
	                                 ==> Convergence Check <==                                  
    
	Measures of convergence in internal coordinates in au.
    
	Criteria marked as inactive (o), active & met (*), and active & unmet ( ).

	----------------------------------------------------------------------------------------------
	   Step    Total Energy     Delta E     Max Force     RMS Force      Max Disp      RMS Disp   
	----------------------------------------------------------------------------------------------
	  Convergence Criteria     1.00e-06 *    3.00e-04 *             o    1.20e-03 *             o
	----------------------------------------------------------------------------------------------
	     4    -273.26238195   -1.29e-05      1.23e-04 *    2.77e-05 o    1.63e-03      5.35e-04 o  ~
	----------------------------------------------------------------------------------------------


INFO:psi

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -273.2623822475437
INFO:psi4.driver.driver:[[ 0.55529409  0.03174622  0.02974007 ...  0.00195484 -0.00010457  0.00029667]
 [ 0.03174622  0.64660119 -0.03765776 ... -0.00025436 -0.00023040 -0.00048097]
 [ 0.02974007 -0.03765776  0.59296448 ... -0.00174505  0.00076656  0.00055998]
 ...
 [ 0.00195484 -0.00025436 -0.00174505 ...  0.09090117 -0.04389428  0.08374233]
 [-0.00010457 -0.00023040  0.00076656 ... -0.04389428  0.11251431 -0.11466418]
 [ 0.00029667 -0.00048097  0.00055998 ...  0.08374233 -0.11466418  0.27119958]]


 '468.9494' '478.7245' '580.0607']


In [ ]:
print(f'equatorial freqs:\n{get_freqs(equatorial_wfn)}')
equatorial_G = psi4.variable('GIBBS FREE ENERGY')
equatorial_Gcorr = psi4.variable('GIBBS FREE ENERGY CORRECTION')

equatorial freqs:
[  162.8195647899053142   239.2799693886845205   258.8374498099099128
   330.1919753972642297   351.4168036054977051   434.5665254940516888
   468.9494166915012556   478.7244539875595137   580.0607387475027963
   823.9044362391172172   851.9171112586307117   903.2763834506127978
   923.6544636421606356   938.1062013045686854   990.1540372581324618
  1043.1071070690470606  1050.8868818363864648  1051.5373551371931171
  1111.6516919809635056  1145.7145238155901552  1165.5827367566641897
  1189.7559513134251574  1221.5583740588324417  1283.5358781636898584
  1321.5428684219291426  1372.0972696147541683  1384.1529094332126988
  1389.2031264589504644  1437.5294110027125498  1440.6769588601046053
  1476.9215458705575656  1502.2157247076802378  1502.7936659576664624
  1508.8633885190095043  1518.8199927837838459  1532.7202548150335133
  1581.0357540154727758  1588.1492660812975828  1593.6421123700001772
  1594.0663336196041655  1595.3202666540007613  1597.0755037250166879
  

In [ ]:
print(equatorial.save_string_xyz())

0 1
 C   -0.336905645406   -1.071358284511   -0.668503615247
 C    1.193285529251   -1.083213559334   -0.655705552660
 C    1.767015742405    0.334784444614   -0.641628686212
 C    1.194920054547    1.154460175737    0.516354219630
 C   -0.335275995892    1.159982347225    0.500243322928
 C   -0.921697828513   -0.257677572212    0.493237548436
 H    2.858119393623    0.300824434795   -0.578316230846
 H    1.542402311701   -1.622171771412    0.232717414596
 H    1.571078199664   -1.635298793109   -1.520599767546
 H   -0.687174016806   -0.642514222397   -1.615726570735
 H   -0.718920713448   -2.095958816470   -0.633566093498
 H    1.544124043900    0.730638039488    1.465082216561
 H    1.573861890305    2.179378813480    0.477467789441
 H   -0.716135743358    1.715129127830    1.362635397136
 H   -0.685469604964    1.694851519937   -0.391444098443
 H   -0.614483505794   -0.747006886685    1.427020861110
 H    1.525589768943    0.831146708930   -1.588932132233
 C   -2.448953059156   -0.2

In [ ]:
show_3D(equatorial)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
show_normal_modes('equatorial.default.1549.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((162.8195647899, 0), (239.2799693887, 1), …

アキシアル置換

In [ ]:
psi4.set_output_file('axial.log')

PosixPath('axial.log')

In [ ]:
axial = psi4.geometry('''
0 1
 C                 -2.15838901   -1.67295376    0.00000000
 C                 -0.64328301   -1.67295376    0.00000000
 C                 -0.09135201   -0.26187576    0.00000000
 C                 -0.64101501    0.54266124    1.16066100
 C                 -2.15614001    0.54332224    1.16017200
 C                 -2.70894001   -0.86729876    1.15887600
 H                  1.02724699   -0.29586676    0.06271400
 H                 -0.27073401   -2.21858776    0.90656200
 H                 -0.26798901   -2.22281276   -0.90191000
 H                 -2.53107701   -1.23992476   -0.96538500
 H                 -2.53398601   -2.72717376    0.06350200
 H                 -0.26848001    0.10781624    2.12527200
 H                 -0.26499201    1.59679824    1.09866600
 H                 -2.53146001    1.09275024    2.06228600
 H                 -2.52799501    1.08992324    0.25384900
 H                 -0.35997001    0.24375724   -0.96454600
 C                 -2.34375843   -1.56157538    2.48410141
 H                 -2.74805066   -1.00326314    3.30247494
 H                 -2.75034420   -2.55128438    2.49210909
 H                 -1.27915043   -1.61256543    2.57849329
 H                 -3.77661875   -0.83383226    1.09689125
 ''')

In [ ]:
_, axial_wfn = optfreq(axial, 'hf/cc-pvdz')

Streaming output truncated to the last 5000 lines.
INFO:psi4.optking.convcheck:
	                                 ==> Convergence Check <==                                  
    
	Measures of convergence in internal coordinates in au.
    
	Criteria marked as inactive (o), active & met (*), and active & unmet ( ).

	----------------------------------------------------------------------------------------------
	   Step    Total Energy     Delta E     Max Force     RMS Force      Max Disp      RMS Disp   
	----------------------------------------------------------------------------------------------
	  Convergence Criteria     1.00e-06 *    3.00e-04 *             o    1.20e-03 *             o
	----------------------------------------------------------------------------------------------
	     4    -273.25850262   -4.11e-05      2.39e-04 *    6.57e-05 o    1.45e-03      5.84e-04 o  ~
	----------------------------------------------------------------------------------------------


INFO:psi

Optimizer: Optimization complete!


INFO:psi4.driver.driver:Return hessian(): -273.258503960182
INFO:psi4.driver.driver:[[ 0.54708913  0.02694584  0.03311149 ... -0.01374665  0.02160277  0.03145299]
 [ 0.02694584  0.64948980 -0.04281271 ...  0.00010546 -0.00084626 -0.00192777]
 [ 0.03311149 -0.04281271  0.59105053 ... -0.00290253  0.00250657  0.00214754]
 ...
 [-0.01374665  0.00010546 -0.00290253 ...  0.34689275 -0.02058986  0.03893949]
 [ 0.02160277 -0.00084626  0.00250657 ... -0.02058986  0.06652584 -0.00449996]
 [ 0.03145299 -0.00192777  0.00214754 ...  0.03893949 -0.00449996  0.07269594]]


 '481.8137' '510.3954']


In [ ]:
print(f'axial freqs:\n{get_freqs(equatorial_wfn)}')
axial_G = psi4.variable('GIBBS FREE ENERGY')
axial_Gcorr = psi4.variable('GIBBS FREE ENERGY CORRECTION')

axial freqs:
[  162.8195647899053142   239.2799693886845205   258.8374498099099128
   330.1919753972642297   351.4168036054977051   434.5665254940516888
   468.9494166915012556   478.7244539875595137   580.0607387475027963
   823.9044362391172172   851.9171112586307117   903.2763834506127978
   923.6544636421606356   938.1062013045686854   990.1540372581324618
  1043.1071070690470606  1050.8868818363864648  1051.5373551371931171
  1111.6516919809635056  1145.7145238155901552  1165.5827367566641897
  1189.7559513134251574  1221.5583740588324417  1283.5358781636898584
  1321.5428684219291426  1372.0972696147541683  1384.1529094332126988
  1389.2031264589504644  1437.5294110027125498  1440.6769588601046053
  1476.9215458705575656  1502.2157247076802378  1502.7936659576664624
  1508.8633885190095043  1518.8199927837838459  1532.7202548150335133
  1581.0357540154727758  1588.1492660812975828  1593.6421123700001772
  1594.0663336196041655  1595.3202666540007613  1597.0755037250166879
  1613.

In [ ]:
print(axial.save_string_xyz())

0 1
 C   -0.599543285462   -0.980802816527   -0.843568635594
 C    0.930382142077   -0.947542055430   -0.917636373153
 C    1.457874855669    0.488881367285   -0.935599768294
 C    0.931966911184    1.292921002247    0.255544857275
 C   -0.597963770013    1.252686351487    0.325960891358
 C   -1.167375361928   -0.177045626520    0.339688017162
 H    2.551390581534    0.490941061830   -0.941013780429
 H    1.359362068346   -1.481122509115   -0.063182862788
 H    1.266671838636   -1.482607530432   -1.810079075202
 H   -1.001474798763   -0.562054274947   -1.773109789146
 H   -0.952230681407   -2.015342504960   -0.795565274027
 H    1.361039518866    0.894100193441    1.180564195104
 H    1.269369755327    2.330836906371    0.186769974396
 H   -0.949534243234    1.802923118932    1.203801351727
 H   -0.999814791807    1.778597990859   -0.547467933613
 H    1.141500811849    0.976109691718   -1.865640956528
 C   -0.959583861438   -0.881795024789    1.685282044342
 H   -1.419766529806   -0.3

In [ ]:
show_3D(axial)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [ ]:
show_normal_modes('axial.default.1549.molden_normal_modes')

interactive(children=(Dropdown(description='Normal mode:', options=((170.3747906613, 0), (216.433826922, 1), (…

##### 自由エネルギー差を推定

In [ ]:
au2kcal = psi4.constants.hartree2kcalmol
diff = au2kcal * (axial_G - equatorial_G)
print(f'free energy difference: {diff: .2f} kcal/mol')

free energy difference:  2.68 kcal/mol


### 高精度でエネルギーを求める場合

In [ ]:
print(equatorial_Gcorr, axial_Gcorr)

0.17953219845659935 0.17992845779974725


In [ ]:
high_level = 'mp2/aug-cc-pvtz'

psi4.set_output_file('high_level_single_point.log')

eq_energy = psi4.energy(high_level, molecule=equatorial)
ax_energy = psi4.energy(high_level, molecule=axial)

INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute energy(): method=mp2, basis=aug-cc-pvtz, molecule=default, nre=328.6064583895363
INFO:psi4.driver.driver:Return energy(): -274.71019631344313
INFO:psi4.driver.task_planner:PLANNING Atomic:  keywords={'SCF__INTS_TOLERANCE': 1e-12, 'NORMAL_MODES_WRITE': 1, 'function_kwargs': {}}
INFO:psi4.driver.driver:Compute energy(): method=mp2, basis=aug-cc-pvtz, molecule=default, nre=332.2284958441912
INFO:psi4.driver.driver:Return energy(): -274.7073035116847


In [ ]:
eq_free_energy = eq_energy + equatorial_Gcorr
ax_free_energy = ax_energy + axial_Gcorr

In [ ]:
diff_free_energy = (ax_free_energy - eq_free_energy) * au2kcal
print(f'free energy difference at high level: {diff_free_energy: .2f} kcal/mol')

free energy difference at high level:  2.06 kcal/mol
